In [1]:
%%writefile custom.css
/* custom.css */

/* Set background color for all widgets */
.tuneStatus {
    /* white background */
    background-color: #ffffff;
}

Overwriting custom.css


In [2]:
from IPython.display import display, HTML
from ray import tune

# Load custom CSS file
css = HTML(
    '<link rel="stylesheet" type="text/css" href="./custom.css">'
)  # make sure the path is correct, it fails silently otherwise
display(css)


def objective(config):
    return -1


tune.run(
    objective,
    config={"aa": tune.uniform(0, 1)},
)

/Users/tijsvandervelden/Development/MADS/Jaar2/Exercises/.venv/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2024-09-22 14:52:00,372	INFO util.py:154 -- Missing packages: ['ipywidgets']. Run `pip install -U ipywidgets`, then restart the notebook server for rich notebook output.
2024-09-22 14:52:00,622	INFO util.py:154 -- Missing packages: ['ipywidgets']. Run `pip install -U ipywidgets`, then restart the notebook server for rich notebook output.
2024-09-22 14:52:01,275	INFO worker.py:1786 -- Started a local Ray instance.
2024-09-22 14:52:01,661	INFO tune.py:253 -- Initializing Ray automatically. For cluster usage or custom Ray initialization, call `ray.init(...)` before `tune.run(...)`.
2024-09-22 14:52:01,662	INFO tune.py:616 -- [output] This uses the legacy output and progress reporter, as Jupyter no

2024-09-22 14:52:02,351	INFO tune.py:1009 -- Wrote the latest version of all result files and experiment state to '/Users/tijsvandervelden/ray_results/objective_2024-09-22_14-52-01' in 0.0014s.
2024-09-22 14:52:02,353	INFO tune.py:1041 -- Total run time: 0.69 seconds (0.68 seconds for the tuning loop).


In [5]:
from pathlib import Path
from typing import Optional
from mads_datasets import DatasetFactoryProvider, DatasetType
import warnings
import mlflow
import torch
from torch import nn
from torch.utils.data import DataLoader
from torch.optim import Adam
from torcheval.metrics import MulticlassAccuracy
from tytorch.trainer import Trainer, EarlyStopping
from torch.nn import CrossEntropyLoss
from loguru import logger
from datetime import datetime
import mlflow.pytorch
import mlflow
import mlflow.pytorch

warnings.simplefilter("ignore", UserWarning)


def set_best_run_tag_and_log_model(
    experiment_name: str, model: nn.Module, metric_name: str, direction: str = "max"
):
    """
    Finds the run with the best metric result in an MLflow experiment (by name), sets a tag 'best_run=True',
    and logs a model to that run.

    Parameters:
    - experiment_name (str): The name of the MLflow experiment.
    - metric_name (str): The name of the metric to evaluate.
    - model_path (str): Path to the PyTorch model (.pth file) to log to the best run.
    - model_class (torch.nn.Module): The model class to load the saved state_dict into.
    - direction (str): The optimization direction, either 'min' or 'max'. Defaults to 'max'.

    """
    # Ensure that direction is valid
    if direction not in ["min", "max"]:
        raise ValueError("Direction must be either 'min' or 'max'")

    # Get experiment_id from experiment_name
    client = mlflow.tracking.MlflowClient()
    experiment = client.get_experiment_by_name(experiment_name)

    if experiment is None:
        raise ValueError(f"Experiment '{experiment_name}' not found.")

    experiment_id = experiment.experiment_id

    # Get all runs in the experiment
    runs = client.search_runs(experiment_id, order_by=[f"metrics.{metric_name}"])

    if not runs:
        print("No runs found in this experiment.")
        return

    # Find the best run based on the direction
    best_run = None
    best_metric = None

    for run in runs:
        metric_value = run.data.metrics.get(metric_name)

        if metric_value is not None:
            if best_run is None:
                best_run = run
                best_metric = metric_value
            else:
                if (direction == "min" and metric_value < best_metric) or (
                    direction == "max" and metric_value > best_metric
                ):
                    best_run = run
                    best_metric = metric_value

    if best_run:
        # Set the tag 'best_run=True' for the best run
        client.set_tag(best_run.info.run_id, "best_run", "True")
        print(
            f"Best run with ID {best_run.info.run_id} has been tagged as the best run with a metric value of {best_metric}."
        )

        # Log the PyTorch model to the best run
        with mlflow.start_run(best_run.info.run_id):
            mlflow.pytorch.log_model(
                pytorch_model=model, artifact_path="logged_models/model"
            )
            print(f"Model has been logged to run {best_run.info.run_id}.")
    else:
        print(f"No valid runs found with the metric '{metric_name}'.")


def getModelfromMLFlow(
    experimentName, best_run: bool = False, runId: Optional[int] = None
):
    experiment = mlflow.get_experiment_by_name(experimentName)

    if experiment:
        experiment_id = experiment.experiment_id
    else:
        raise Exception(f"Experiment '{experimentName}' does not exist.")

    if runId is None:
        if best_run:
            # Filter runs with the tag "best_run" set to True
            runs = mlflow.search_runs(
                experiment_ids=[experiment_id],
                filter_string="tags.best_run = 'True'",
                order_by=["start_time DESC"],
            )
        else:
            # Get the most recent run
            runs = mlflow.search_runs(
                experiment_ids=[experiment_id], order_by=["start_time DESC"]
            )

        if not runs.empty:
            last_run = runs.iloc[0]  # Get the most recent run
            runId = last_run.run_id
            logger.info(f"Last run ID: {runId}")
            logger.info(f"Run details:\n{last_run}")
        else:
            logger.info(f"No runs found for experiment '{experimentName}'.")

    model_uri = f"runs:/{runId}/logged_models/model"
    param_uri = f"runs:/{runId}/params.json"
    param_dict = mlflow.artifacts.load_dict(param_uri)
    state_dict = mlflow.pytorch.load_model(model_uri).state_dict()
    return param_dict, state_dict

/Users/tijsvandervelden/Development/MADS/Jaar2/Exercises/.venv/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2024-09-22 20:00:31,274	INFO util.py:154 -- Missing packages: ['ipywidgets']. Run `pip install -U ipywidgets`, then restart the notebook server for rich notebook output.
2024-09-22 20:00:31,311	INFO util.py:154 -- Missing packages: ['ipywidgets']. Run `pip install -U ipywidgets`, then restart the notebook server for rich notebook output.


In [3]:
if torch.backends.mps.is_available() and torch.backends.mps.is_built():
    device = torch.device("mps")
    print("Using MPS")
elif torch.cuda.is_available():
    device = "cuda:0"
    print("using cuda")
else:
    device = "cpu"
    print("using cpu")

Using MPS


In [5]:
class NeuralNetwork(nn.Module):
    def __init__(self, config):
        super(NeuralNetwork, self).__init__()
        self.flatten = nn.Flatten()
        self.linear_relu_stack = nn.Sequential(
            nn.Linear(28 * 28, config["h1"]),
            nn.ReLU(),
            nn.Dropout(p=0.2),
            nn.Linear(config["h1"], config["h2"]),
            nn.ReLU(),
            nn.Dropout(p=0.2),
            nn.Linear(config["h2"], 10),
        )

    def forward(self, x):
        x = self.flatten(x)
        logits = self.linear_relu_stack(x)
        return logits

In [6]:
class cnn(nn.Module):
    def __init__(self, config: dict):
        super().__init__()
        self.in_channels = config["input_size"][1]
        self.input_size = config["input_size"]

        self.convolutions = nn.Sequential(
            nn.Conv2d(
                self.in_channels, config["filters"], kernel_size=3, stride=1, padding=1
            ),
            nn.ReLU(),
            nn.MaxPool2d(kernel_size=2),
            nn.Conv2d(
                config["filters"], config["filters"], kernel_size=3, stride=1, padding=0
            ),
            nn.ReLU(),
            nn.MaxPool2d(kernel_size=2),
            nn.Conv2d(
                config["filters"], config["filters"], kernel_size=3, stride=1, padding=0
            ),
            nn.ReLU(),
            nn.MaxPool2d(kernel_size=2),
        )

        activation_map_size = self._conv_test(self.input_size)

        self.agg = nn.AvgPool2d(activation_map_size)

        self.dense = nn.Sequential(
            nn.Flatten(),
            nn.Linear(config["filters"], config["h1"]),
            nn.ReLU(),
            nn.Linear(config["h1"], config["h2"]),
            nn.ReLU(),
            nn.Linear(config["h2"], 10),
        )

    def _conv_test(self, input_size):
        x = torch.ones(input_size, dtype=torch.float32)
        x = self.convolutions(x)
        return x.shape[-2:]

    def forward(self, x):
        x = self.convolutions(x)
        x = self.agg(x)
        logits = self.dense(x)
        return logits

tune

In [7]:
n_epochs = 10
n_trials = 50
batch_size = 32

tuningmetric = "valid_loss"
tuninggoal = "min"

search_space = {
    "lr": tune.loguniform(1e-5, 1e-3),
    "filters": tune.qrandint(32, 128, 16),
    "h1": tune.qrandint(32, 256, 16),
    "h2": tune.qrandint(16, 128, 16),
    "input_size": (batch_size, 1, 28, 28),
}

timestamp = datetime.now().strftime("%Y-%m-%d-%H:%M:S")
experiment_path = f"tune-{timestamp}"

modelClass = cnn

datasetfactory = DatasetFactoryProvider.create_factory(DatasetType.FASHION)

In [8]:
from ray import train, tune
from ray.tune.schedulers import ASHAScheduler
from ray.tune.search.hyperopt import HyperOptSearch
from ray.tune import TuneConfig
from ray.air.integrations.mlflow import MLflowLoggerCallback


def tune_func(config):
    datasets = datasetfactory.create_dataset()
    trainloader = DataLoader(datasets["train"], batch_size=batch_size, shuffle=True)
    testloader = DataLoader(datasets["valid"], batch_size=batch_size, shuffle=True)

    model = modelClass(config)
    model = model.to(device)

    trainer = Trainer(
        model=model,
        loss_fn=CrossEntropyLoss(),
        metrics=[MulticlassAccuracy()],
        optimizer=Adam(model.parameters(), lr=config["lr"]),
        device=device,
    )

    mlflow.log_params(config)
    trainer.fit(n_epochs, trainloader, testloader)


mlflow.set_tracking_uri("sqlite:///mlflow.db")
mlflow.set_experiment(experiment_path)

tuner = tune.Tuner(
    tune_func,
    param_space=search_space,
    tune_config=TuneConfig(
        mode=tuninggoal,
        scheduler=ASHAScheduler(),
        search_alg=HyperOptSearch(),
        metric=tuningmetric,
        num_samples=n_trials,
    ),
    run_config=train.RunConfig(
        storage_path=Path("./ray_tuning_results").resolve(),
        name=experiment_path,
        callbacks=[
            MLflowLoggerCallback(
                tracking_uri=mlflow.get_tracking_uri(),
                experiment_name=experiment_path,
                save_artifact=True,
            )
        ],
    ),
)
results = tuner.fit()

best_result = results.get_best_result(tuningmetric, tuninggoal)

model = modelClass(best_result.config)  # Initialize your model class
model.load_state_dict(
    torch.load(Path(best_result.checkpoint.path) / "model.pth")
)  # Load the saved weights
set_best_run_tag_and_log_model(experiment_path, model, tuningmetric, tuninggoal)

(tune_func pid=41618) 2024-09-22 14:52:06.843 | INFO     | mads_datasets.base:download_data:121 - Folder already exists at /Users/tijsvandervelden/.cache/mads_datasets/fashionmnist
(tune_func pid=41618) 2024-09-22 14:52:06.844 | INFO     | mads_datasets.base:download_data:124 - File already exists at /Users/tijsvandervelden/.cache/mads_datasets/fashionmnist/fashionmnist.pt
(tune_func pid=41618) /Users/tijsvandervelden/Development/MADS/Jaar2/Exercises/.venv/lib/python3.11/site-packages/mads_datasets/factories/torchfactories.py:71: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that co

2024-09-22 15:02:07,102	INFO tune.py:1009 -- Wrote the latest version of all result files and experiment state to '/Users/tijsvandervelden/Development/MADS/Jaar2/Exercises/ray_tuning_results/tune-2024-09-22-14:52:S' in 0.0189s.
2024-09-22 15:02:07,108	INFO tune.py:1041 -- Total run time: 602.11 seconds (602.07 seconds for the tuning loop).
/var/folders/mz/c75dd4q509n8kkcgqr48dc640000gn/T/ipykernel_41519/1583405337.py:59: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unles

Best run with ID 10828b8feb2f4454adf59190e80612b5 has been tagged as the best run with a metric value of 0.26202080148858387.


2024/09/22 15:02:08 WARNING mlflow.utils.environment: Failed to resolve installed pip version. ``pip`` will be added to conda.yaml environment spec without a version specifier.
2024/09/22 15:02:08 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.


Model has been logged to run 10828b8feb2f4454adf59190e80612b5.


train

In [4]:
fashionfactory = DatasetFactoryProvider.create_factory(DatasetType.FASHION)
datasets = fashionfactory.create_dataset()
trainloader = DataLoader(datasets["train"], batch_size=batch_size, shuffle=True)
testloader = DataLoader(datasets["valid"], batch_size=batch_size, shuffle=True)

# modelClass = NeuralNetwork
params, state = getModelfromMLFlow(experiment_path, True)

timestamp = datetime.now().strftime("%Y-%m-%d-%H:%M:S")
experiment_path = f"train-{timestamp}"
mlflow.set_tracking_uri("sqlite:///mlflow.db")
mlflow.set_experiment(experiment_path)


model = modelClass(params).to(device)
trainer = Trainer(
    model=model,
    loss_fn=CrossEntropyLoss(),
    metrics=[MulticlassAccuracy()],
    optimizer=Adam(model.parameters(), lr=params["lr"]),
    early_stopping=EarlyStopping(5, 0.01, "min"),
    device=device,
)

with mlflow.start_run():
    mlflow.log_params(params)
    trainer.fit(20, trainloader, testloader)
    mlflow.pytorch.log_model(model, artifact_path="logged_models/model")
mlflow.end_run()

NameError: name 'DatasetFactoryProvider' is not defined